# Random Walks in Ecology: Movement of Large Herbivores
### EPS 109 Final Project - Adam Angle

This notebook is a demonstration of how we can use random walks to model the behavior of deer in an arbitrary field through just a few parameters.

**References:**

Berthelot, G., Saïd, S. & Bansaye, V. A random walk model that accounts for space occupation and movements of a large herbivore. Sci Rep 11, 14061 (2021). https://doi.org/10.1038/s41598-021-93387-2 (Shared Article Link: https://rdcu.be/dr3MZ)



In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter

# Define a new PRNG to use for this notebook (with optional preset seed for reproducibility)
rng = np.random.default_rng()

In [ ]:
class Animal:
    def __init__(self, x, y, rng, pI, pF, ps, mu=3.0, sigma=1.0):
        self.x, self.y = x, y  # X_i
        self.x_prev, self.y_prev = x, y  # X_{i-1}
        self.rng = rng
        self.pI = pI
        self.pF = pF
        self.ps = ps
        self.mu = mu
        self.sigma = sigma
        self.qtyX = 8 + pI + pF + ps
        self._x_pts = []
        self._y_pts = []
        
    def piecewise_f(self, Xf_x=0, Xf_y=0):
        d = self.rng.normal(self.mu, self.sigma)
        x = self.rng.uniform(low=0, high=self.qtyX)
        alpha = 0
        if 0 <= x < 8:
            alpha = self.rng.uniform(low=0.0, high=2 * np.pi)
        elif 8 <= x < 8 + self.pI:
            alpha = np.arctan2(self.y - self.y_prev, self.x - self.x_prev)
        elif 8 + self.pI <= x < 8 + self.pI + self.ps:
            return self.x, self.y
        else:
            alpha = np.arctan2(Xf_y - self.y, Xf_x - self.x)
        
        return self.x + d * np.cos(alpha), self.y + d * np.sin(alpha)
            
    def move_to(self, x, y):
        self._x_pts.append(x)
        self._y_pts.append(y)
        self.x_prev, self.y_prev = self.x, self.y
        self.x, self.y = x, y
        
    def get_points(self):
        return self._x_pts, self._y_pts

In [ ]:
# Single simulation MP4
%matplotlib qt
metadata = dict(title='Animal Simulation', artist='Adam Angle')
writer = FFMpegWriter(fps=60, metadata=metadata)
fig = plt.figure(dpi=300)

# Simulates a new animal starting from a central origin. 
def simulate_animated(runs, steps, get_animal_func, goal):
    with writer.saving(fig, "animation1.mp4", dpi=300):
        animals = [get_animal_func(i) for i in range(runs)]
        for step in range(steps):
            if (step%10==0): print(step,end='')
            print('.',end='')
            fig.clear()
            ax = fig.add_subplot()
            for i, animal in enumerate(animals):
                new_X = animal.piecewise_f(*goal)
                animal.move_to(*new_X)
                ax.plot(*animal.get_points())
            plt.xlim(-100, 100)
            plt.ylim(-100, 100)
            plt.suptitle('50 animals over 500 steps with zeroed parameters')
            plt.draw()
            plt.pause(0.01)
            writer.grab_frame()
            
simulate_animated(50, 500, lambda i: Animal(0., 0., rng, 0., 0., 0.), (50, 50))

In [ ]:
# Multiple simulation MP4 with multithreading
%matplotlib qt
from threading import Thread
plt.rcParams['text.usetex'] = True

metadata = dict(title='Animal Simulation - Parameter Demo', artist='Adam Angle')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure(figsize=(8, 6), dpi=400, layout='tight')
axs = fig.subplot_mosaic([["plt1", "plt2", "plt3", "plt4"],
                         ["plt5", "plt6", "plt7", "plt8"],
                         ["plt9", "plt10", "plt11", "plt12"]])

goal_point = (50, 50)

all_graphs = [
    (lambda: Animal(0., 0., rng, 0., 0., 0.), 'plt1', goal_point),
    (lambda: Animal(0., 0., rng, 10., 0., 0.), 'plt2', goal_point),
    (lambda: Animal(0., 0., rng, 50., 0., 0.), 'plt3', goal_point),
    (lambda: Animal(0., 0., rng, 150., 0., 0.), 'plt4', goal_point),
    (lambda: Animal(0., 0., rng, 0., 0., 0.), 'plt5', goal_point),
    (lambda: Animal(0., 0., rng, 0., 0., 10.), 'plt6', goal_point),
    (lambda: Animal(0., 0., rng, 0., 0., 100.), 'plt7', goal_point),
    (lambda: Animal(0., 0., rng, 0., 0., 1000.), 'plt8', goal_point),
    (lambda: Animal(0., 0., rng, 0., 0., 0.), 'plt9', goal_point),
    (lambda: Animal(0., 0., rng, 0., 0.3, 0.), 'plt10', goal_point),
    (lambda: Animal(0., 0., rng, 0., 1.6, 0.), 'plt11', goal_point),
    (lambda: Animal(0., 0., rng, 0., 10., 0.), 'plt12', goal_point),
]

# Simulates a new animal starting from a central origin. 
def simulate_new_animated(graphs, fig, axs, runs, steps):
    
    # Create new animals for each simulation
    simulations = [[g[0]() for _ in range(runs)] for g in graphs]
    
    # Create flag variables for worker thread signals
    threads = [None] * len(graphs)
    
    def worker_thread(sim):
        ax = axs[graphs[sim][1]]
        ax.clear()
        cur_sim = simulations[sim]
        goal = graphs[sim][2]
        for i, animal in enumerate(cur_sim):
            new_X = animal.piecewise_f(*goal)
            animal.move_to(*new_X)
            ax.plot(*animal.get_points())
        ax.plot(0, 0, 'ko', label='Start')
        ax.plot(*goal, 'k*', label='Goal')
        ax.set_xlim(-125, 125)
        ax.set_ylim(-125, 125)
        ax.get_xaxis().set_visible(False)
        ax.get_yaxis().set_visible(False)
        ax.set_title(f'$p_I={cur_sim[0].pI}$, $p_s={cur_sim[0].ps}$, $p_F={cur_sim[0].pF}$')
        ax.title.set_size(10)
        if sim == len(graphs) - 1:
            handles, labels = ax.get_legend_handles_labels()
            plt.figlegend(handles, labels, loc='upper right', ncol=2)

    
    with writer.saving(fig, "animation2.mp4", dpi=400):
        for step in range(steps):
            if (step%10==0): print(step,end='')
            print('.',end='')
            
            for sim in range(len(graphs)):
                threads[sim] = Thread(target=worker_thread, args=(sim,))
                threads[sim].start()
                
            for i in range(len(threads)):
                threads[i].join()
            
            plt.suptitle(f'{len(graphs)} simulations of {runs} animals moving {steps} steps each')
            plt.draw()
            writer.grab_frame()
            
simulate_new_animated(all_graphs, fig, axs, 50, 100)

In [ ]:
# Simulation of observed red deer using included variable values.
%matplotlib qt
metadata = dict(title='GPS Animal Simulation', artist='Adam Angle')
writer = FFMpegWriter(fps=60, metadata=metadata)
fig = plt.figure(dpi=300)

# See https://www.nature.com/articles/s41598-021-93387-2/tables/2
animals = [
    #      X   Y   RNG  p_I   p_F   p_s   mu    sigma
    Animal(0., 0., rng, 0.01, 0.01, 2.01, 2.94, 1.01),
    Animal(0., 0., rng, 0.06, 0.13, 1.44, 3.15, 0.97),
    Animal(0., 0., rng, 0.12, 0.05, 1.70, 3.07, 1.04),
    Animal(0., 0., rng, 0.10, 0.06, 1.52, 3.10, 0.98),
    Animal(0., 0., rng, 0.22, 0.24, 1.66, 3.03, 1.06)
]
goal = (50, 50)
steps = 500

# Simulates a new animal starting from a central origin. 
with writer.saving(fig, "animation3.mp4", dpi=300):
    for step in range(steps):
        if (step%10==0): print(step,end='')
        print('.',end='')
        fig.clear()
        ax = fig.add_subplot()
        for i, animal in enumerate(animals):
            new_X = animal.piecewise_f(*goal)
            animal.move_to(*new_X)
            ax.plot(*animal.get_points(), label=f'Deer {i+1}')
        ax.plot(0, 0, 'ko', label='Start')
        ax.plot(*goal, 'k*', label='Goal')
        plt.xlim(-100, 100)
        plt.ylim(-100, 100)
        plt.legend()
        plt.suptitle('Simulation using observed parameter values')
        plt.draw()
        plt.pause(0.01)
        writer.grab_frame()